In [2]:
# Libraries

In [1]:
import os
import pandas as pd
from pandas import read_csv
import numpy as np
import re
from io import StringIO

In [24]:
# ---- File Management ----
# CSV Models
metricasDeepGroup = read_csv("C:/Users/TimeSeriesUser/Desktop/MetaLearning/DeepLearning/metricasDeepGroupOrderDif.csv",delimiter=",")
# Predictions made by model from the TS
predictionsListRavel_DL = np.load("C:/Users/TimeSeriesUser/Desktop/MetaLearning/DeepLearning/predictionsListRavel_DL.npy", allow_pickle=True)
# Real Values for each TS
realList_DL = np.load("C:/Users/TimeSeriesUser/Desktop/MetaLearning/DeepLearning/realListRavel_DL.npy", allow_pickle=True)


df = metricasDeepGroup.groupby(['id_serie', 'output', 'rep']).mean()


#ff = metricasDeepGroup.loc[metricasDeepGroup['id_serie'] == 39]
#ff = ff.loc[ff['rep'] == 0]
#ff = ff.loc[ff['output'] == 12]
#ff

Unnamed: 0  input     sMAPE         MAE      MAPE
id_serie output rep                                                   
39       3      0           0.0   12.0  0.059146  177.707682  0.110673
                1           0.0   12.0  0.023519   69.966200  0.044736
                2           0.0   12.0  0.034656  107.933681  0.070899
         12     0           0.0   12.0  0.036981   27.844402  0.076338
                1           0.0   12.0  0.049211   38.318187  0.086785

In [142]:


def metrics(pre, real):
    
    # sMAPE
    sMAPE=np.sum(np.abs(pre-real))/np.sum((pre+real))
    
    #MAE
    # Len en Real
    MAE=np.mean(np.abs(pre-real)/len(real))
        
    #MAPE
    MAPE=np.mean(np.abs((real-pre)/real))
    
    
    return [sMAPE, MAE, MAPE]


# Input: dataframe-> TS Dataframe, realValues-> Real Values for each TS, predictionValues -> Predictions made by model from the TS
# Output: List of real and predictions averages into a data frame

def averageDataListGenerator(dataframe, realValues, predictionValues):
    # List of averages
    temp_list = []
    temp_list_averages = []
    #Metrics List
    temp_metricsList = []
    #List of averages for NPY
    realNPY = []
    predNPY = []
    for i,row in dataframe.iterrows():
        print("  ")
        print("Iter #", i)
        print("  ")
        #print(row["id_serie"], row["id_model"], row["rep"], row["output"])
        df = dataframe.loc[dataframe['id_serie'] == row.loc["id_serie"]]
        df = df.loc[df['rep'] == row.loc["rep"]]
        df = df.loc[df['output'] == row.loc["output"]]
        realAve = []
        predicAve = []
        temp_list_averages = []
        
        for j,row in df.iterrows():
            print(row["id_serie"], row["rep"], row["output"])
            # Promediar arreglos 1 x 1.
            realAve.append(realValues[j])
            predicAve.append(predictionValues[j])
        
        
        realAve = calcAverages(realAve)
        predicAve = calcAverages(predicAve)
        temp_metricsList = metrics(realAve,predicAve)
        #print(metricsList)
        #Agregamos datos generales de la serie de tiempo
        temp_list_averages.append(row["id_serie"])
        temp_list_averages.append(row["rep"])
        temp_list_averages.append(row["output"])
        #Agregamos los promedios reales de la serie de tiempo
        #temp_list_averages.append(realAve)
        realNPY.append(realAve)
        #Agregamos los promedios de predicciones de la serie de tiempo
        #temp_list_averages.append(predicAve)
        predNPY.append(predNPY)
        #Agregamos las metricas calculadas con las pred y los reales de la serie de tiempo
        temp_list_averages.append(temp_metricsList[0])
        temp_list_averages.append(temp_metricsList[1])
        temp_list_averages.append(temp_metricsList[2])
        temp_list.append(temp_list_averages)
        #print("TS AVERAGES\n")
        #print(temp_list_averages)
        #print("TEMP LIST\n")
        #print(temp_list)
  
    # Create the pandas DataFrame
    df = pd.DataFrame(temp_list, columns=["id_serie","rep","output","sMAPE", "MAE", "MAPE"])
    df.to_csv("C:/Users/TimeSeriesUser/Desktop/MetaLearning/DeepLearning/DL_averages.csv", index = False, header=True)
    #np.save("real_assembly_ts.npy",np.array(realNPY))
    #np.save("pred_assembly_ts.npy",np.array(predNPY))
    return  

# Calculate Averages for a list
def calcAverages(averages):
    #print(averages)
    a = np.zeros(shape=(len(averages[0])), dtype='float32')
    
    for listAve in averages:
        for j in range(0,len(averages[0])):
            a[j] += listAve[j]
    
    return a/len(averages)
            
#averageDataListGenerator(metricasDeepGroup,realList_DL,predictionsListRavel_DL)
df = read_csv("C:/Users/TimeSeriesUser/Desktop/MetaLearning/DeepLearning/DL_averages.csv",delimiter=",")
df = df.drop_duplicates()


In [143]:
# dataf: CSV DADO
# dataf2: CSV GEN
def averageDataListGenerator(dataf, dataf2):
    temp_df = []
    for i,row in dataf2.iterrows():
        values = []
        
        print("Iter",i)
        #print(row["id_serie"], row["rep"], row["output"],row["sMAPE"],row["MAE"],row["MAPE"])
        print("")
        df = dataf.loc[dataf['id_serie'] == row.loc["id_serie"]]
        df = df.loc[df['rep'] == row.loc["rep"]]
        df = df.loc[df['output'] == row.loc["output"]]
        df = df.groupby(['id_serie', 'output', 'rep']).mean()
        #print(df.head())
        
        #id_serie
        values.append(int(row["id_serie"]))
        #rep
        values.append(int(row["rep"]))
        #output
        values.append(int(row["output"]))
        #sMAPE
        sMAPE_df1 = float(df['sMAPE'])
        sMAPE_df2 = float(row.loc['sMAPE'])
        values.append(((sMAPE_df1 + sMAPE_df2)/2))
        #MAE
        MAE_df1 = float(df['MAE'])
        MAE_df2 = float(row.loc['MAE'])
        values.append(((MAE_df1 + MAE_df2)/2))
        #MAPE
        MAPE_df1 = float(df['MAPE'])
        MAPE_df2 = float(row.loc['MAPE'])
        values.append(((MAPE_df1 + MAPE_df2)/2))
        print(values)
        # Add to list
        temp_df.append(values)
           
    # Create the pandas DataFrame
    df = pd.DataFrame(temp_df, columns=["id_serie","rep","output","sMAPE", "MAE", "MAPE"])
    df.to_csv("C:/Users/TimeSeriesUser/Desktop/MetaLearning/DeepLearning/Final_averages.csv", index = False, header=True)
    return


    
averageDataListGenerator(metricasDeepGroup,df)

Iter
39.0 0.0 12.0 0.03585644 27.050295 0.07084332

                     Unnamed: 0  input     sMAPE        MAE      MAPE
id_serie output rep                                                  
39       12     0           0.0   12.0  0.036981  27.844402  0.076338
[39, 0, 12, 0.03641893383333333, 27.44734847333333, 0.07359076816666667]
Iter
45.0 0.0 12.0 0.06562445 38.33241 0.12156711

                     Unnamed: 0  input     sMAPE        MAE      MAPE
id_serie output rep                                                  
45       12     0           1.0   12.0  0.075119  44.404841  0.172975
[45, 0, 12, 0.07037186816666666, 41.36862555333334, 0.14727105966666665]
Iter
99.0 0.0 12.0 0.01016425 3.8146327 0.020434804

                     Unnamed: 0  input    sMAPE       MAE      MAPE
id_serie output rep                                                
99       12     0           2.0   12.0  0.00952  3.574509  0.018606
[99, 0, 12, 0.009842078, 3.6945709095000003, 0.019520339333333334]
Iter
10

                     Unnamed: 0  input     sMAPE       MAE      MAPE
id_serie output rep                                                 
779      12     0          39.0   12.0  0.010245  4.184569  0.020114
[779, 0, 12, 0.010931299333333333, 4.4612258085, 0.021759768166666665]
Iter
780.0 0.0 12.0 0.016261507 5.1123157 0.032846253

                     Unnamed: 0  input     sMAPE       MAE     MAPE
id_serie output rep                                                
780      12     0          40.0   12.0  0.019119  5.996676  0.03744
[780, 0, 12, 0.017690285166666667, 5.554495772166666, 0.035143005]
Iter
782.0 0.0 12.0 0.009320447 6.2568073 0.018732134

                     Unnamed: 0  input     sMAPE       MAE      MAPE
id_serie output rep                                                 
782      12     0          41.0   12.0  0.009781  6.567209  0.019234
[782, 0, 12, 0.009550774833333334, 6.412008024666667, 0.018983273000000002]
Iter
790.0 0.0 12.0 0.022342969 46.19342 0.045397952

    

                     Unnamed: 0  input     sMAPE       MAE      MAPE
id_serie output rep                                                 
1654     12     0          82.0   12.0  0.005309  2.553044  0.010804
[1654, 0, 12, 0.005704167466666667, 2.7451929535, 0.011464488]
Iter
1673.0 0.0 12.0 0.0043607336 0.79098344 0.008683786

                     Unnamed: 0  input     sMAPE       MAE      MAPE
id_serie output rep                                                 
1673     12     0          83.0   12.0  0.004615  0.837339  0.009301
[1673, 0, 12, 0.004488004299999999, 0.814161244, 0.0089921975]
Iter
1693.0 0.0 12.0 0.013237344 3.439543 0.02678661

                     Unnamed: 0  input     sMAPE       MAE      MAPE
id_serie output rep                                                 
1693     12     0          84.0   12.0  0.012434  3.235932  0.024404
[1693, 0, 12, 0.012835886833333334, 3.337737622166667, 0.0255954215]
Iter
1710.0 0.0 12.0 0.0029575378 0.72700924 0.005911716

              

                     Unnamed: 0  input     sMAPE        MAE     MAPE
id_serie output rep                                                 
2482     12     0         121.0   12.0  0.016742  14.472651  0.03458
[2482, 0, 12, 0.014832927, 12.762007800500001, 0.030118277166666665]
Iter
2506.0 0.0 12.0 0.00941711 5.7833877 0.01898289

                     Unnamed: 0  input    sMAPE       MAE     MAPE
id_serie output rep                                               
2506     12     0         122.0   12.0  0.01395  8.550842  0.02782
[2506, 0, 12, 0.011683685, 7.167114653333334, 0.023401239833333334]
Iter
2516.0 0.0 12.0 0.05095755 5.8028846 0.10046035

                     Unnamed: 0  input     sMAPE       MAE      MAPE
id_serie output rep                                                 
2516     12     0         123.0   12.0  0.061717  6.901107  0.125511
[2516, 0, 12, 0.05633727733333333, 6.351995840833333, 0.1129854705]
Iter
2527.0 0.0 12.0 0.059006087 29.552214 0.12580101

                 

                     Unnamed: 0  input     sMAPE        MAE      MAPE
id_serie output rep                                                  
3490     12     0         164.0   12.0  0.023976  13.422592  0.045913
[3490, 0, 12, 0.0249650445, 13.948280028333333, 0.049673437333333334]
Iter
3497.0 0.0 12.0 0.029438822 19.08872 0.06081525

                     Unnamed: 0  input    sMAPE       MAE      MAPE
id_serie output rep                                                
3497     12     0         165.0   12.0  0.02324  15.09366  0.044808
[3497, 0, 12, 0.026339162, 17.091190009166667, 0.052811635]
Iter
3515.0 0.0 12.0 0.0025919355 2.0056322 0.0051866826

                     Unnamed: 0  input     sMAPE       MAE      MAPE
id_serie output rep                                                 
3515     12     0         166.0   12.0  0.003766  2.914242  0.007524
[3515, 0, 12, 0.003178822083333333, 2.4599372751666664, 0.006355171466666667]
Iter
3529.0 0.0 12.0 0.107690334 17.361097 0.22011359

    

...

                     Unnamed: 0  input     sMAPE        MAE     MAPE
id_serie output rep                                                 
43320    3      2        1815.0   12.0  0.009306  43.298702  0.01839
[43320, 2, 3, 0.009100132833333333, 42.385625766666664, 0.018188574333333332]
Iter
43352.0 2.0 3.0 0.0038850312 28.61849 0.0077841394

                     Unnamed: 0  input     sMAPE        MAE      MAPE
id_serie output rep                                                  
43352    3      2        1816.0   12.0  0.010957  80.573857  0.021885
[43352, 2, 3, 0.007420769266666666, 54.596173525, 0.0148345482]
Iter
43355.0 2.0 3.0 0.0073817135 53.247395 0.014897556

                     Unnamed: 0  input     sMAPE         MAE      MAPE
id_serie output rep                                                   
43355    3      2        1817.0   12.0  0.014189  100.840965  0.027754
[43355, 2, 3, 0.010785173416666667, 77.04418, 0.021325975]
Iter
43357.0 2.0 3.0 0.011008982 8.203125 0.022276914




                     Unnamed: 0  input     sMAPE        MAE      MAPE
id_serie output rep                                                  
44599    3      2        1860.0   12.0  0.024879  79.626926  0.047653
[44599, 2, 3, 0.024111211, 77.82694034166667, 0.047767365666666665]
Iter
44602.0 2.0 3.0 0.019624708 17.998373 0.040117174

                     Unnamed: 0  input     sMAPE        MAE      MAPE
id_serie output rep                                                  
44602    3      2        1861.0   12.0  0.015335  14.116697  0.030061
[44602, 2, 3, 0.017480022166666668, 16.057534849833335, 0.035089313999999996]
Iter
44606.0 2.0 3.0 0.024226526 72.630264 0.049735654

                     Unnamed: 0  input     sMAPE        MAE      MAPE
id_serie output rep                                                  
44606    3      2        1862.0   12.0  0.025723  75.801701  0.049219
[44606, 2, 3, 0.0249750115, 74.21598226500001, 0.049477135166666665]
Iter
44618.0 2.0 3.0 0.03795498 102.333824

                     Unnamed: 0  input     sMAPE         MAE      MAPE
id_serie output rep                                                   
45761    3      2        1902.0   12.0  0.167185  128.115508  0.223907
[45761, 2, 3, 0.16658149533333333, 127.72023393333333, 0.3050466571666667]
Iter
45848.0 2.0 3.0 0.14345129 70.01274 0.30102444

                     Unnamed: 0  input    sMAPE        MAE      MAPE
id_serie output rep                                                 
45848    3      2        1903.0   12.0  0.14408  69.158595  0.287162
[45848, 2, 3, 0.14376554633333333, 69.585667555, 0.29409301083333333]
Iter
45860.0 2.0 3.0 0.16676143 578.17206 0.2823054

                     Unnamed: 0  input     sMAPE        MAE      MAPE
id_serie output rep                                                  
45860    3      2        1904.0   12.0  0.194755  714.00538  0.475489
[45860, 2, 3, 0.18075804033333331, 646.0887200666666, 0.378897339]
Iter
45871.0 2.0 3.0 0.02031609 99.90814 0.03976138


                     Unnamed: 0  input    sMAPE          MAE      MAPE
id_serie output rep                                                   
46988    3      2        1947.0   12.0  0.11269  1230.276982  0.312383
[46988, 2, 3, 0.10386579483333333, 1097.8581410666666, 0.24893873383333331]
Iter
46996.0 2.0 3.0 0.13062368 708.243 0.26969016

                     Unnamed: 0  input     sMAPE         MAE      MAPE
id_serie output rep                                                   
46996    3      2        1948.0   12.0  0.126976  690.378074  0.294719
[46996, 2, 3, 0.12879991783333333, 699.3105371833333, 0.282204417]
Iter
47014.0 2.0 3.0 0.04139188 30.123339 0.07974127

                     Unnamed: 0  input     sMAPE       MAE      MAPE
id_serie output rep                                                 
47014    3      2        1949.0   12.0  0.056085  41.53496  0.115472
[47014, 2, 3, 0.04873836116666666, 35.829149290000004, 0.09760655016666667]
Iter
47067.0 2.0 3.0 0.059241477 209.9068 

[47865, 2, 3, 0.016419176, 17.77869812, 0.032703450833333335]
Iter
47869.0 2.0 3.0 0.039427906 279.9669 0.078160666

                     Unnamed: 0  input     sMAPE       MAE      MAPE
id_serie output rep                                                 
47869    3      2        1990.0   12.0  0.038157  270.3261  0.076621
[47869, 2, 3, 0.03879226683333334, 275.1464997833333, 0.07739095766666666]
Iter
47871.0 2.0 3.0 0.015866404 10.977431 0.031214997

                     Unnamed: 0  input     sMAPE       MAE      MAPE
id_serie output rep                                                 
47871    3      2        1991.0   12.0  0.015898  11.03852  0.032731
[47871, 2, 3, 0.015882320166666665, 11.007975481833332, 0.03197281083333334]
Iter
47874.0 2.0 3.0 0.014303775 9.928982 0.028222183

                     Unnamed: 0  input     sMAPE       MAE      MAPE
id_serie output rep                                                 
47874    3      2        1992.0   12.0  0.016616  11.56802  0.033993

In [144]:
df = read_csv("C:/Users/TimeSeriesUser/Desktop/MetaLearning/DeepLearning/Final_averages.csv",delimiter=",")
df

id_serie  rep  output     sMAPE         MAE      MAPE
0            39    0      12  0.036419   27.447348  0.073591
1            45    0      12  0.070372   41.368626  0.147271
2            99    0      12  0.009842    3.694571  0.019520
3           109    0      12  0.016508    6.450189  0.032855
4           111    0      12  0.036929   10.361651  0.073570
...         ...  ...     ...       ...         ...       ...
11995     47917    2       3  0.005771   38.414206  0.011511
11996     47920    2       3  0.017453  116.322286  0.034765
11997     47928    2       3  0.010418   68.009298  0.020941
11998     47947    2       3  0.026859  229.147226  0.055075
11999     47993    2       3  0.044262  180.484504  0.084422

[12000 rows x 6 columns]